此 .ipynb为按照行级，获得预测正确和错误的不同行级元素的贡献值分布

In [1]:
import time
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import re

import torch
import torch.nn as nn
from transformers import RobertaTokenizer, RobertaForSequenceClassification
from torch.utils.data import DataLoader, RandomSampler, SequentialSampler
from transformers import AdamW, get_linear_schedule_with_warmup
from torch.nn.utils.rnn import pad_sequence
from torch.utils.data import Dataset, TensorDataset


from captum.attr import visualization as viz
from captum.attr import LayerConductance, LayerIntegratedGradients
from captum.attr import configure_interpretable_embedding_layer, remove_interpretable_embedding_layer

# 解决服务器挂掉的问题
import os
os.environ["KMP_DUPLICATE_LIB_OK"] = "TRUE"

In [2]:
# device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
device = torch.device( "cpu")

In [3]:
MAX_LEN = 1024
MAX_EPOCHS = 10
BATCH_SIZE = 4
LEARNING_RATE = 1e-5
NUM_CLASSES = 2
WEIGTH_DECAY = 1e-3

In [4]:
def retrieve_test_data():
    test_param = pd.read_json("D:/BERT_learing/code_comment_inconsistency_detection/data/param/train.json")
    test_return = pd.read_json("D:/BERT_learing/code_comment_inconsistency_detection/data/return/train.json")
    test_summary = pd.read_json("D:/BERT_learing/code_comment_inconsistency_detection/data/summary/train.json")
    test_df = pd.concat([test_summary,test_param, test_return], axis=0)
    test_df = test_df.reset_index(drop=True)
    return test_df
test_df = retrieve_test_data()

In [5]:
def get_lines_count(df):
    line_counts = []
    for i in range(len(df)):
        string = df.loc[i]['new_code_raw']
        line_count = len(string.split('\n'))
        line_counts.append(line_count)
    df['line_counts'] = line_counts
    return df
test_df = get_lines_count(test_df)
test_df.head()

id  label comment_type  \
0  grails-plugins_grails-plugin-converters-5-Asso...      1      Summary   
1                   jitsi_jitsi-4343-FirstSentence-0      0      Summary   
2   dropwizard_metrics-26-Associations-FirstSentence      1      Summary   
3                google_ExoPlayer-92-FirstSentence-0      0      Summary   
4  slachiewicz_orekit-main-661-Associations-First...      1      Summary   

                                     old_comment_raw  \
0  Parses the given JSON and returns ether a JSON...   
1      Loads an image from a given image identifier.   
2  Creates a new  CounterMetric and registers it ...   
3  Derives a sample format corresponding to a giv...   
4              Revert a rotation/rotation rate pair.   

                               old_comment_subtokens  \
0  [parses, the, given, json, and, returns, ether...   
1  [loads, an, image, from, a, given, image, iden...   
2  [creates, a, new, counter, metric, and, regist...   
3  [derives, a, sample, format, corresponding, to...   
4  [revert, a, rotation, /, rotation, rate, pair, .]   

                                     new_comment_raw  \
0  Parses the given JSON and returns either a JSO...   
1      Loads an image from a given image identifier.   
2  Creates a new  com.yammer.metrics.core.Counter...   
3  Derives a sample format corresponding to a giv...   
4  Revert a rotation/rotation rate/ rotation acce...   

                               new_comment_subtokens  \
0  [parses, the, given, json, and, returns, eithe...   
1  [loads, an, image, from, a, given, image, iden...   
2  [creates, a, new, com, ., yammer, ., metrics, ...   
3  [derives, a, sample, format, corresponding, to...   
4  [revert, a, rotation, /, rotation, rate, /, ro...   

                 span_minimal_diff_comment_subtokens  \
0  [<REPLACE_OLD>, ether, <REPLACE_NEW>, either, ...   
1                                                 []   
2  [<INSERT_OLD_KEEP_BEFORE>, new, <INSERT_NEW_KE...   
3                                                 []   
4  [<REPLACE_OLD>, pair, <REPLACE_NEW>, /, rotati...   

                                        old_code_raw  \
0      public static JSONElement parse(InputStrea...   
1      public static byte[] getImageInBytes(Strin...   
2      public static CounterMetric newCounter(Cla...   
3    private static Format getSampleFormat(Format...   
4      public AngularCoordinates revert() {\n    ...   

                                  old_code_subtokens  \
0  [public, static, jsonelement, parse, (, input,...   
1  [public, static, byte, [, ], get, image, in, b...   
2  [public, static, counter, metric, new, counter...   
3  [private, static, format, get, sample, format,...   
4  [public, angular, coordinates, revert, (, ), {...   

                                        new_code_raw  \
0      public static JSONElement parse(InputStrea...   
1      public static byte[] getImageInBytes(Strin...   
2      public static Counter newCounter(Class<?> ...   
3    private static Format getSampleFormat(Format...   
4      public AngularCoordinates revert() {\n    ...   

                                  new_code_subtokens  \
0  [public, static, jsonelement, parse, (, input,...   
1  [public, static, byte, [, ], get, image, in, b...   
2  [public, static, counter, new, counter, (, cla...   
3  [private, static, format, get, sample, format,...   
4  [public, angular, coordinates, revert, (, ), {...   

                            span_diff_code_subtokens  \
0  [<KEEP>, public, static, jsonelement, parse, (...   
1  [<KEEP>, public, static, byte, [, ], get, imag...   
2  [<KEEP>, public, static, counter, <KEEP_END>, ...   
3  [<KEEP>, private, static, format, get, sample,...   
4  [<KEEP>, public, angular, coordinates, revert,...   

                           token_diff_code_subtokens  line_counts  
0  [<KEEP>, public, <KEEP>, static, <KEEP>, jsone...            5  
1  [<KEEP>, public, <KEEP>, static, <KEEP>, byte,...           23  
2  [<KEEP>, public,

In [6]:
def remove_last(df):
    for i in range(len(df)):
        string = df.loc[i]['old_comment_raw']
        df['old_comment_raw'][i] = string.rstrip('.')
    return df
test_df = remove_last(test_df)

C:\Users\TEA\AppData\Local\Temp\ipykernel_12064\2027904842.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['old_comment_raw'][i] = string.rstrip('.')
C:\Users\TEA\AppData\Local\Temp\ipykernel_12064\2027904842.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['old_comment_raw'][i] = string.rstrip('.')
C:\Users\TEA\AppData\Local\Temp\ipykernel_12064\2027904842.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['old_commen

C:\Users\TEA\AppData\Local\Temp\ipykernel_12064\2027904842.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['old_comment_raw'][i] = string.rstrip('.')
C:\Users\TEA\AppData\Local\Temp\ipykernel_12064\2027904842.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['old_comment_raw'][i] = string.rstrip('.')
C:\Users\TEA\AppData\Local\Temp\ipykernel_12064\2027904842.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['old_commen

C:\Users\TEA\AppData\Local\Temp\ipykernel_12064\2027904842.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['old_comment_raw'][i] = string.rstrip('.')
C:\Users\TEA\AppData\Local\Temp\ipykernel_12064\2027904842.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['old_comment_raw'][i] = string.rstrip('.')
C:\Users\TEA\AppData\Local\Temp\ipykernel_12064\2027904842.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['old_commen

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)

C:\Users\TEA\AppData\Local\Temp\ipykernel_12064\2027904842.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['old_comment_raw'][i] = string.rstrip('.')
C:\Users\TEA\AppData\Local\Temp\ipykernel_12064\2027904842.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['old_comment_raw'][i] = str

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)

C:\Users\TEA\AppData\Local\Temp\ipykernel_12064\2027904842.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['old_comment_raw'][i] = string.rstrip('.')
C:\Users\TEA\AppData\Local\Temp\ipykernel_12064\2027904842.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['old_comment_raw'][i] = str

C:\Users\TEA\AppData\Local\Temp\ipykernel_12064\2027904842.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['old_comment_raw'][i] = string.rstrip('.')
C:\Users\TEA\AppData\Local\Temp\ipykernel_12064\2027904842.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['old_comment_raw'][i] = string.rstrip('.')
C:\Users\TEA\AppData\Local\Temp\ipykernel_12064\2027904842.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['old_commen

C:\Users\TEA\AppData\Local\Temp\ipykernel_12064\2027904842.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['old_comment_raw'][i] = string.rstrip('.')
C:\Users\TEA\AppData\Local\Temp\ipykernel_12064\2027904842.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['old_comment_raw'][i] = string.rstrip('.')
C:\Users\TEA\AppData\Local\Temp\ipykernel_12064\2027904842.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['old_commen

C:\Users\TEA\AppData\Local\Temp\ipykernel_12064\2027904842.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['old_comment_raw'][i] = string.rstrip('.')
C:\Users\TEA\AppData\Local\Temp\ipykernel_12064\2027904842.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['old_comment_raw'][i] = string.rstrip('.')
C:\Users\TEA\AppData\Local\Temp\ipykernel_12064\2027904842.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['old_commen

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [7]:
train_df_1 = test_df[610:611]
train_df_2 = test_df[716:717]
train_df_4 = test_df[363:364]
test_df = pd.concat([train_df_1,train_df_2,train_df_4], axis=0)
test_df = test_df.reset_index(drop=True)

In [8]:
df_clean = test_df
df_clean.head()

id  label comment_type  \
0  orientechnologies_orientdb-1949-FirstSentence-0      1      Summary   
1  spring_projects_spring_boot-882-FirstSentence-0      0      Summary   
2            raphw_byte_buddy-1042-FirstSentence-0      0      Summary   

                                     old_comment_raw  \
0  Returns a OrientBaseGraph implementation from ...   
1  Creates a  exception tag based on the  Class#g...   
2  Creates a  net.bytebuddy.implementation.Defaul...   

                               old_comment_subtokens  \
0  [returns, a, orient, base, graph, implementati...   
1  [creates, a, exception, tag, based, on, the, c...   
2  [creates, a, net, ., bytebuddy, ., implementat...   

                                     new_comment_raw  \
0  Returns a Transactional OrientGraph implementa...   
1  Creates a  exception tag based on the  Class#g...   
2  Creates a  net.bytebuddy.implementation.Defaul...   

                               new_comment_subtokens  \
0  [returns, a, transactional, orient, graph, imp...   
1  [creates, a, exception, tag, based, on, the, c...   
2  [creates, a, net, ., bytebuddy, ., implementat...   

                 span_minimal_diff_comment_subtokens  \
0  [<INSERT_OLD_KEEP_BEFORE>, a, <INSERT_NEW_KEEP...   
1                                                 []   
2                                                 []   

                                        old_code_raw  \
0    public static OrientBaseGraph getGraph() {\n...   
1  \tpublic static Tag exception(Throwable except...   
2      public static Implementation prioritize(It...   

                                  old_code_subtokens  \
0  [public, static, orient, base, graph, get, gra...   
1  [public, static, tag, exception, (, throwable,...   
2  [public, static, implementation, prioritize, (...   

                                        new_code_raw  \
0    public static OrientBaseGraph getGraph() {\n...   
1  \tpublic static Tag exception(Throwable except...   
2      public static Implementation prioritize(It...   

                                  new_code_subtokens  \
0  [public, static, orient, base, graph, get, gra...   
1  [public, static, tag, exception, (, throwable,...   
2  [public, static, implementation, prioritize, (...   

                            span_diff_code_subtokens  \
0  [<KEEP>, public, static, orient, base, graph, ...   
1  [<KEEP>, public, static, tag, exception, (, th...   
2  [<KEEP>, public, static, implementation, prior...   

                           token_diff_code_subtokens  line_counts  
0  [<KEEP>, public, <KEEP>, static, <KEEP>, orien...            8  
1  [<KEEP>, public, <KEEP>, static, <KEEP>, tag, ...            8  
2  [<KEEP>, public, <KEEP>, static, <KEEP>, imple...            8

In [9]:
code_list = df_clean['new_code_raw']

In [10]:
code_list[0]

'  public static OrientBaseGraph getGraph() {\n    ODatabaseRecord database = ODatabaseRecordThreadLocal.INSTANCE.get();\n    if (!(database instanceof ODatabaseDocumentTx))\n      database = new ODatabaseDocumentTx((ODatabaseRecordTx) database);\n\n    return new OrientGraph((ODatabaseDocumentTx) database);\n  }\n'

In [11]:
df_clean.loc[0]['new_code_raw']

'  public static OrientBaseGraph getGraph() {\n    ODatabaseRecord database = ODatabaseRecordThreadLocal.INSTANCE.get();\n    if (!(database instanceof ODatabaseDocumentTx))\n      database = new ODatabaseDocumentTx((ODatabaseRecordTx) database);\n\n    return new OrientGraph((ODatabaseDocumentTx) database);\n  }\n'

In [12]:
len(df_clean)

3

In [13]:
# model = torch.load('save_GCBmodel.pt',map_location=torch.device('cuda:0'))
model = torch.load('D:/BERT_learing/CCDP/for_captum/save_model/save_GCBmodel.pt',map_location=torch.device('cpu'))

model.to(device)

RobertaForSequenceClassification(
  (roberta): RobertaModel(
    (embeddings): RobertaEmbeddings(
      (word_embeddings): Embedding(50265, 768, padding_idx=1)
      (position_embeddings): Embedding(514, 768, padding_idx=1)
      (token_type_embeddings): Embedding(1, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (encoder): RobertaEncoder(
      (layer): ModuleList(
        (0-11): 12 x RobertaLayer(
          (attention): RobertaAttention(
            (self): RobertaSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (output): RobertaSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
             

In [14]:
import torch
print(torch.__version__)
print(torch.version.cuda)
print(torch.cuda.is_available())  #输出为True，则安装无误


2.3.1+cpu
None
False


In [15]:
device

device(type='cpu')

In [16]:
tokenizer = RobertaTokenizer.from_pretrained("D:/BERT_learing/code_comment_inconsistency_detection/graphcodebert")

In [17]:
model.roberta.embeddings

RobertaEmbeddings(
  (word_embeddings): Embedding(50265, 768, padding_idx=1)
  (position_embeddings): Embedding(514, 768, padding_idx=1)
  (token_type_embeddings): Embedding(1, 768)
  (LayerNorm): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
  (dropout): Dropout(p=0.1, inplace=False)
)

In [18]:
model.roberta.encoder.layer[0]

RobertaLayer(
  (attention): RobertaAttention(
    (self): RobertaSelfAttention(
      (query): Linear(in_features=768, out_features=768, bias=True)
      (key): Linear(in_features=768, out_features=768, bias=True)
      (value): Linear(in_features=768, out_features=768, bias=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (output): RobertaSelfOutput(
      (dense): Linear(in_features=768, out_features=768, bias=True)
      (LayerNorm): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
  )
  (intermediate): RobertaIntermediate(
    (dense): Linear(in_features=768, out_features=3072, bias=True)
    (intermediate_act_fn): GELUActivation()
  )
  (output): RobertaOutput(
    (dense): Linear(in_features=3072, out_features=768, bias=True)
    (LayerNorm): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
    (dropout): Dropout(p=0.1, inplace=False)
  )
)

In [19]:
input_embeddings = model.get_input_embeddings()

In [20]:
# predict和squad_pos_forward_func可以合成一个
def predict(inputs, position_ids=None, attention_mask=None):
    output = model(inputs,
                   position_ids=position_ids,
                  attention_mask=attention_mask )
    
    prediction = output.logits
    prediction_1 = nn.functional.softmax(prediction, dim=1)
    prediction = prediction_1.max(1).values
    out = torch.argmax(prediction_1, dim=-1)
    # prediction：每个输入样本的最大预测概率。
    # out：预测的类别标签。
    # prediction_1：所有类别的预测概率。    
    return prediction,out,prediction_1

In [21]:
def squad_pos_forward_func(inputs,position_ids=None, attention_mask=None, position=0):
    pred ,_,_= predict(inputs,
                     position_ids=position_ids,
                   attention_mask=attention_mask)
    return pred

In [22]:
ref_token_id = tokenizer.pad_token_id # 0
sep_token_id = tokenizer.sep_token_id # 101
cls_token_id = tokenizer.cls_token_id # 102
ref_token_id,sep_token_id,cls_token_id

(1, 2, 0)

In [23]:
# 注意长度
def truncate(ids,len_tru = 512):
    return ids[:len_tru] if len(ids) > len_tru else ids

In [24]:
# 这是单个数据的处理方式，应该要想数据集应该怎么处理
def construct_input_ref_pair(comment,AST_type,  ref_token_id, sep_token_id, cls_token_id):
    comment = tokenizer.encode(comment, add_special_tokens=False,truncation=True,max_length=512)
    AST_type = tokenizer.encode(AST_type, add_special_tokens=False,truncation=True,max_length=512)
    # construct input token ids
    input_ids = [cls_token_id] + comment + [sep_token_id] + AST_type + [sep_token_id]

    # construct reference token ids 
    ref_input_ids = [cls_token_id] + [ref_token_id] * len(comment) + [sep_token_id] + \
        [ref_token_id] * len(AST_type) + [sep_token_id]
    input_ids = truncate(input_ids)
    ref_input_ids = truncate(ref_input_ids)
    return torch.tensor([input_ids], device=device), torch.tensor([ref_input_ids], device=device), len(comment)

def construct_input_ref_token_type_pair(input_ids, sep_ind=0):
    seq_len = input_ids.size(1)
    token_type_ids = torch.tensor([[0 if i <= sep_ind else 1 for i in range(seq_len)]], device=device)
    ref_token_type_ids = torch.zeros_like(token_type_ids, device=device)# * -1
    return token_type_ids, ref_token_type_ids

def construct_input_ref_pos_id_pair(input_ids):
    seq_length = input_ids.size(1)
    position_ids = torch.arange(seq_length, dtype=torch.long, device=device)
    # we could potentially also use random permutation with `torch.randperm(seq_length, device=device)`
    ref_position_ids = torch.zeros(seq_length, dtype=torch.long, device=device)

    position_ids = position_ids.unsqueeze(0).expand_as(input_ids)
    ref_position_ids = ref_position_ids.unsqueeze(0).expand_as(input_ids)
    return position_ids, ref_position_ids

def construct_attention_mask(input_ids):
    return torch.ones_like(input_ids)

def construct_whole_bert_embeddings(input_ids, ref_input_ids, \
                                    token_type_ids=None, ref_token_type_ids=None, \
                                    position_ids=None, ref_position_ids=None):
    input_embeddings = model.roberta.embeddings(input_ids, token_type_ids=token_type_ids, position_ids=position_ids)
    ref_input_embeddings = model.roberta.embeddings(ref_input_ids, token_type_ids=ref_token_type_ids, position_ids=ref_position_ids)
    
    return input_embeddings, ref_input_embeddings

In [25]:
def input_data_list(AST_list,comment_list):
    input_ids_all = []
    ref_input_ids_all = []
    position_ids_all = []
    attention_mask_all = []
    token_type_ids_all = []
    all_tokens_all = []
    for i in range(len(AST_list)):
        input_ids, ref_input_ids, comment_len = construct_input_ref_pair(comment_list[i],AST_list[i], ref_token_id,\
                                                                         sep_token_id, cls_token_id)
        token_type_ids, ref_token_type_ids = construct_input_ref_token_type_pair(input_ids, comment_len)
        position_ids, ref_position_ids = construct_input_ref_pos_id_pair(input_ids)
        attention_mask = construct_attention_mask(input_ids)
        
        indices = input_ids[0].detach().tolist()
        
        all_tokens = []                                       ###
        for _, token in enumerate(indices):
            all_tokens.append(tokenizer.decode([token]))
        
        input_ids_all.append(input_ids)
        ref_input_ids_all.append(ref_input_ids)
        position_ids_all.append(position_ids)
        attention_mask_all.append(attention_mask)
        token_type_ids_all.append(token_type_ids)
        all_tokens_all.append(all_tokens)

    return input_ids_all,ref_input_ids_all,position_ids_all,attention_mask_all,token_type_ids_all,all_tokens_all 

In [26]:
# 前k个贡献最高的word 和 token_type 和 position
# return value为归因贡献值  indices为词对应的索引  top_tokens为 词或位置或token_type
def get_topk_attributed_tokens(attrs,all_token_t, k=5):
    values_max, indices_max = torch.topk(attrs, k)
    top_tokens_max = [all_token_t[idx] for idx in indices_max]
    values_min, indices_min = torch.topk(attrs, k, largest=False)
    top_tokens_min = [all_token_t[idx] for idx in indices_min] 
    
    return top_tokens_max, values_max, indices_max,top_tokens_min,values_min,indices_min


In [27]:
import re
import string

def split_punctuation(s):
    # 使用正则表达式匹配连续的标点符号或者字母和标点符号之间的位置
    splits = re.finditer(r'(?<=\w)(?=[{}])|(?<=[{}])(?=\w)'.format(string.punctuation, string.punctuation), s)
    
    # 获取所有分割位置
    split_positions = [match.start() for match in splits]
    
    # 在分割位置插入空格
    for pos in reversed(split_positions):
        s = s[:pos] + ' ' + s[pos:]
        
    s = s.replace("< s >", "<s>")
    s = s.replace("</ s >", "</s>")
    return s


In [28]:
# 从 all_tokens 还原为 原单词 ，并且计算归因值
def get_restore_words(code,comment,input_ids,all_tokens,attribution_num):
    all_tokens_decode = tokenizer.decode(input_ids)
    len_all_tokens_decode = len(all_tokens_decode) + 4
    # 使用decode获得的序列，去掉分词之后的空格    例 ' a' -> 'a'
    all_tokens_clean = []
    for token in all_tokens:
        s_without_leading_space = token.lstrip()
        all_tokens_clean.append(s_without_leading_space)
#     print('all_tokens_clean:\n',all_tokens_clean)
#     print('all_tokens_clean:\n',len(all_tokens_clean))
    

    # 获得 code_comment_baseline
    code = tokenizer.encode(code, add_special_tokens=False,truncation=True,max_length=512)
    comment = tokenizer.encode(comment, add_special_tokens=False,truncation=True,max_length=512)
    code_decode = tokenizer.decode(code)
    comment_decode = tokenizer.decode(comment)
    
    code_comment_baseline = tokenizer.decode(tokenizer.cls_token_id) + ' '+ comment_decode \
                            + ' '+ tokenizer.decode(tokenizer.sep_token_id) + ' ' + code_decode \
                            + ' ' + tokenizer.decode(tokenizer.sep_token_id)
    
    code_comment_baseline = code_comment_baseline[:len_all_tokens_decode]
    code_comment_baseline = split_punctuation(code_comment_baseline)
    code_comment_baseline = code_comment_baseline.split()

#     print('code_comment_baseline:\n',code_comment_baseline)
#     print('code_comment_baseline_len:\n',len(code_comment_baseline))

    
    # 获得 相邻有几个token合并在一块的列表times  为了以后再计算attribute时求和
    times = []
    token_index = 0
    for code_comment in code_comment_baseline:
        temp = ''
        time = 0
        while temp != code_comment:
            temp = temp + all_tokens_clean[token_index]
            token_index = token_index + 1
            time = time + 1
        times.append(time)
#     print('times:\n',times)
    
    attribute_sum = []
    start = 0
    for time in times:
        end = start + time
        attribute = sum(attribution_num[start:end]) / time
        attribute_sum.append(attribute)
        start = end
#     print('attribute_sum:\n',attribute_sum)
    return code_comment_baseline ,attribute_sum 

In [29]:
def get_line_code_and_attribute(code,code_all_tokens,attributions_num):
    # 特殊符号前  加空格
    code = split_punctuation(code)
    
    # 把  行前空格去掉  便于单词与行之间匹配
    code = [line.lstrip() for line in code.splitlines()]
    code = '\n'.join(code)  
    code_lineList = code.split('\n')
    code_lineList = [' '.join(x.split()) for x in code_lineList]
    # 有空行，把空行去掉
    code_lineList = [item for item in code_lineList if item != '']
    
    attribute = []
    i = 0  
    for code_line in code_lineList:
        count = 0
        if i < len(code_all_tokens):
            temp = code_all_tokens[i]
            attr = attributions_num[i]
            i = i + 1
        while((i < len(code_all_tokens)) and(temp != code_line)):
            attr = attr + attributions_num[i]
            temp = temp + ' ' + code_all_tokens[i]
            i = i + 1
            count = count + 1
        attribute.append(attr/count)

    return code_lineList,attribute   

In [30]:
def remove_before_and_including(lst, element):
    if element in lst:
        index = lst.index(element)
        lst_c = lst[index+1:]
        if element in lst_c:
            lst_c.remove(element)
        return lst_c
    else:
        return lst
    
def remove_after_including(lst, element):
    if element in lst:
        index = lst.index(element)
        return lst[:index + 1]
    else:
        return lst

In [31]:
def get_comment_attribution(all_tokens,attributions_num):
    
    comment_all_tokens = remove_after_including(all_tokens,'</s>')   
    index = all_tokens.index('</s>')
    comment_all_tokens = comment_all_tokens[1:-1]
    attribute_comment = attributions_num[1:index]
    
    return comment_all_tokens,attribute_comment

In [32]:
def final_all_attribute(code,all_tokens,attributions_num):
    # 删除 all_token 列表中的<s>注释</s>  </s>
    code_all_tokens = remove_before_and_including(all_tokens,'</s>')
    comment_all_tokens = remove_after_including(all_tokens,'</s>')  
    index = all_tokens.index('</s>')
    attribute_comment = attributions_num[:index+1]
#     print(attribute_comment)
    
    attribute_code = attributions_num[index+1:-1]
#     print(attribute_code,len(attribute_code))
    code_lineList_token,attribute_num_code = get_line_code_and_attribute(code,code_all_tokens,attribute_code)
##     print(attribute_num_code)
    attribute_num_code = torch.stack(attribute_num_code)
    
    new_all_tokens = comment_all_tokens + code_lineList_token
    attributions_num_all = torch.cat((attribute_comment, attribute_num_code))

#     attributions_num_all = attribute_comment + attribute_num_code
#     print(len(attribute_comment),len(attribute_num_code))
#     print(new_all_tokens)
    return new_all_tokens,attributions_num_all,code_lineList_token,attribute_num_code

In [33]:
from captum.attr import LayerIntegratedGradients
from captum.attr import visualization as viz

lig = LayerIntegratedGradients(squad_pos_forward_func,input_embeddings)

In [34]:
def interpret_sentence_2(code,comment,old_code,input_ids,ref_input_ids, token_type_ids,\
                         position_ids, attention_mask, all_tokens):
    pre ,out,_ = predict(input_ids,  position_ids=position_ids,attention_mask=attention_mask)
  
    attributions_ig, delta_ig = lig.attribute(input_ids, baselines=ref_input_ids,\
                           additional_forward_args=(position_ids,attention_mask,0),return_convergence_delta=True,internal_batch_size=8)
    
    attributions = attributions_ig.sum(dim=2).squeeze(0)
    attributions = attributions / torch.norm(attributions)
#     print(delta_ig)
#     print(attributions)
    try:
        all_tokens ,attributions = get_restore_words(code,comment,input_ids[0],all_tokens,attributions)     # 合并为一个单词
        attributions = torch.tensor(attributions)
        
        comment_token,comment_attribute = get_comment_attribution(all_tokens,attributions)
       
        # code_lineList_token 和 attribute_num_code 用于后续统计分析
        new_all_tokens,attributions_num_all,code_lineList_token,attribute_num_code = final_all_attribute(code,all_tokens,attributions)

        return out,code_lineList_token,attribute_num_code,comment_token,comment_attribute 
    except Exception as e:
#         pass
        print("解析错误")
        return -1,_,_,_,_

判断行级贡献值分布情况，将一些特殊语句变为一个具有代表性的词

In [35]:
# 单个示例获取各种statement 的函数
def get_ifstatement(code_line,attribution_num):
    code_contains_if = [(i, s) for i, s in enumerate(code_line) if 'if' in s]
    attr_contains_if = [attribution_num[code_contains_if[i][0]] for i in range(len(code_contains_if))]
    return code_contains_if,attr_contains_if
def get_forstatement(code_line,attribution_num):
    code_contains_for = [(i, s) for i, s in enumerate(code_line) if 'for' in s]
    attr_contains_for = [attribution_num[code_contains_for[i][0]] for i in range(len(code_contains_for))]
    return code_contains_for,attr_contains_for
def get_whilestatement(code_line,attribution_num):
    code_contains_while = [(i, s) for i, s in enumerate(code_line) if 'while' in s]
    attr_contains_while = [attribution_num[code_contains_while[i][0]] for i in range(len(code_contains_while))]
    return code_contains_while,attr_contains_while
def get_variableDeclaration(code_line,attribution_num):
    code_contains_new = [(i, s) for i, s in enumerate(code_line) if 'new' in s]
    attr_contains_new = [attribution_num[code_contains_new[i][0]] for i in range(len(code_contains_new))]
    return code_contains_new,attr_contains_new
def get_expression(code_line,attribution_num):
    code_contains_exp = [(i, s) for i, s in enumerate(code_line) if '=' in s]
    attr_contains_exp = [attribution_num[code_contains_exp[i][0]] for i in range(len(code_contains_exp))]
    return code_contains_exp,attr_contains_exp
def get_try_catch(code_line,attribution_num):
    code_contains_try_catch = [(i, s) for i, s in enumerate(code_line) if 'try' in s]
    attr_contains_try_catch = [attribution_num[code_contains_try_catch[i][0]] for i in range(len(code_contains_try_catch))]
    return code_contains_try_catch,attr_contains_try_catch
def get_return(code_line,attribution_num):
    code_contains_return = [(i, s) for i, s in enumerate(code_line) if 'return' in s]
    attr_contains_return = [attribution_num[code_contains_return[i][0]] for i in range(len(code_contains_return))]
    return code_contains_return,attr_contains_return
def get_MethodDeclaration(code_line,attribution_num):
    code_contains_Method = [code_line[0]]
    attr_contains_Method = [attribution_num[0]]
    return code_contains_Method,attr_contains_Method

In [36]:
# 集成到数据集中 , 对返回值进行数据分析 , 六个列表试着画小提琴图
def get_all_statement(code_line_list,attribution_num_list):
    ifstatement ,ifstatement_num = [],[]
    forstatement ,forstatement_num = [],[]
    whilestatement ,whilestatement_num = [],[]
    variableDeclaration ,variableDeclaration_num = [],[]
    expression ,expression_num = [],[]
    trystatement ,trystatement_num = [],[]
    returnstatement ,returnstatement_num = [],[]
    MethodDeclaration ,MethodDeclaration_num = [],[]
    for (code_line,attribution_num) in zip(code_line_list,attribution_num_list):
#         print(code_line,attribution_num)
        code_contains_if,attr_contains_if = get_ifstatement(code_line,attribution_num)
        code_contains_for,attr_contains_for = get_forstatement(code_line,attribution_num)
        code_contains_while,attr_contains_while = get_whilestatement(code_line,attribution_num)
        code_contains_new,attr_contains_new = get_variableDeclaration(code_line,attribution_num)
        code_contains_exp,attr_contains_exp = get_expression(code_line,attribution_num)
        code_contains_try_catch,attr_contains_try_catch = get_try_catch(code_line,attribution_num)
        code_contains_return,attr_contains_return = get_return(code_line,attribution_num)
        code_contains_Method,attr_contains_Method = get_MethodDeclaration(code_line,attribution_num)
        
        ifstatement.append(code_contains_if ) if code_contains_if != [] else None
        ifstatement_num.append(attr_contains_if ) if attr_contains_if != [] else None
        forstatement.append(code_contains_for ) if code_contains_for != [] else None
        forstatement_num.append(attr_contains_for) if attr_contains_for != [] else None
        whilestatement.append(code_contains_while ) if code_contains_while != [] else None
        whilestatement_num.append(attr_contains_while ) if attr_contains_while != [] else None
        variableDeclaration.append(code_contains_new ) if code_contains_new != [] else None
        variableDeclaration_num.append(attr_contains_new) if attr_contains_new != [] else None
        expression.append(code_contains_exp ) if code_contains_exp != [] else None
        expression_num.append(attr_contains_exp ) if attr_contains_exp != [] else None  
        
        trystatement.append(code_contains_try_catch ) if code_contains_try_catch != [] else None
        trystatement_num.append(attr_contains_try_catch ) if attr_contains_try_catch != [] else None 
        
        returnstatement.append(code_contains_return ) if code_contains_return != [] else None
        returnstatement_num.append(attr_contains_return ) if attr_contains_return != [] else None               
        MethodDeclaration.append(code_contains_Method ) if code_contains_Method != [] else None
        MethodDeclaration_num.append(attr_contains_Method ) if attr_contains_Method != [] else None
        
    return ifstatement_num,forstatement_num,whilestatement_num,variableDeclaration_num,expression_num,\
           trystatement_num,returnstatement_num,MethodDeclaration_num

In [37]:
# 展开内部列表,便于统计
def flattened_list(lst):
    flattened_lst = [item for sublist in lst for item in sublist]
    return flattened_lst

In [38]:
def analyse_line_attribution(df):
    code_list = df['new_code_raw']
    comment_list = df['old_comment_raw']
    code_list_old = df['old_code_raw']
    ground_lable = df['label']
    
    input_ids_all,ref_input_ids_all,position_ids_all,attention_mask_all,\
    token_type_ids_all,all_tokens_all= input_data_list(code_list,comment_list)
    
    code_lineList_token_true = []
    attribute_num_code_true = []
    comment_token_true = []
    comment_attribute_true = []
    index_true = []
    
    code_lineList_token_false = []
    attribute_num_code_false = []
    comment_token_false = []
    comment_attribute_false = []
    index_false = []

    for i in range(len(code_list)): 
        out,code_lineList_token,attribute_num_code,comment_token,comment_attribute  \
        = interpret_sentence_2(code_list[i],comment_list[i],\
                               code_list_old[i],input_ids_all[i],\
                               ref_input_ids_all[i], token_type_ids_all[i],\
                               position_ids_all[i],attention_mask_all[i], all_tokens_all[i])
        if out != -1:
            if out == ground_lable[i]:
                index_true.append(i)
                code_lineList_token_true.append(code_lineList_token)
                attribute_num_code_true.append(attribute_num_code)
                comment_token_true.append(comment_token)
                comment_attribute_true.append(comment_attribute)

            else :
                index_false.append(i)
                code_lineList_token_false.append(code_lineList_token)
                attribute_num_code_false.append(attribute_num_code)
                comment_token_false.append(comment_token)
                comment_attribute_false.append(comment_attribute)
    return index_true,index_false,\
           code_lineList_token_true,attribute_num_code_true,\
           code_lineList_token_false,attribute_num_code_false,\
           comment_token_true,comment_attribute_true,\
           comment_token_false,comment_attribute_false

In [39]:
index_true,index_false,\
code_lineList_token_true,attribute_num_code_true,\
code_lineList_token_false,attribute_num_code_false,\
comment_token_true,comment_attribute_true,\
comment_token_false,comment_attribute_false\
= analyse_line_attribution(df_clean)

In [40]:
comment_token_true, comment_attribute_true

([['Returns',
   'a',
   'OrientBaseGraph',
   'implementation',
   'from',
   'the',
   'current',
   'database',
   'in',
   'thread',
   'local'],
  ['Creates',
   'a',
   'exception',
   'tag',
   'based',
   'on',
   'the',
   'Class',
   '#',
   'getSimpleName',
   '()',
   'simple',
   'name',
   'of',
   'the',
   'class',
   'of',
   'the',
   'given',
   'exception']],
 [tensor([ 0.0178,  0.0099, -0.1307,  0.1523,  0.0984,  0.0844,  0.2520,  0.2362,
           0.0642,  0.2528,  0.2140], dtype=torch.float64),
  tensor([-0.3184,  0.0036, -0.1429,  0.0660, -0.2384, -0.1024, -0.0537, -0.0894,
           0.0292,  0.1316,  0.0202,  0.1145, -0.1035, -0.0301,  0.0669,  0.0414,
          -0.0345,  0.0647, -0.0015,  0.0348], dtype=torch.float64)])

In [41]:
comment_token_false, comment_attribute_false

([['Creates',
   'a',
   'net',
   '.',
   'bytebuddy',
   '.',
   'implementation',
   '.',
   'DefaultMethodCall',
   'implementation',
   'which',
   'searches',
   'the',
   'given',
   'list',
   'of',
   'interface',
   'types',
   'for',
   'a',
   'suitable',
   'default',
   'method',
   'in',
   'their',
   'order']],
 [tensor([ 0.0105, -0.0508,  0.4256,  0.1999,  0.1734,  0.1609,  0.0149,  0.0205,
          -0.0329,  0.0531,  0.1886,  0.0128,  0.0262,  0.0080, -0.0565,  0.0092,
          -0.0034,  0.0162,  0.0077,  0.0801,  0.0129,  0.0669,  0.0731,  0.0055,
           0.0656,  0.0144], dtype=torch.float64)])